# Load Packages

In [2]:
import pandas as pd
import seaborn as sns
import plotly.express as px
import matplotlib.pyplot as plt
import plotly.graph_objs as go
import plotly.figure_factory as ff
import pulp
import os
import sys
import scipy 
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor
from sklearn.pipeline import Pipeline
from sklearn.model_selection import KFold, RandomizedSearchCV, train_test_split, GridSearchCV
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score, make_scorer
from sklearn.linear_model import LinearRegression
from tqdm import tqdm
import statsmodels.api as sm
import unittest
from pandas.testing import assert_frame_equal
import importlib

parent_dir = os.path.abspath('..')
sys.path.insert(0, parent_dir)

from src.preprocessing import PreprocessData
from src.integer_programming import optimise_team
from src.player_stats import PlayerStats
from src.player_stats import TeamStats
from src.player_stats import CombineTeamAndPlayers


## Preprocessing

## Forecasting for an individual player

While the data contains several variables already, there are many potential new variables to add such as:
- Opponent team's finishing position in previous season.
- Rolling average of teams position over last 5 games
- Rolling average of opponent teams position over last 5 games
- Current difference in league position between teams
- Add in a rolling total of the teams points and compare it to the opponents team (likely percentage wise difference)
- Column with the number of minutes played in the past 7 days (will need domestic cup/european/international data)


Initally when taking the previous x games, we're taking the previous x games the PLAYER was involved in.  This shouldn't be a problem most of the time, however could create a couple of issues should the player transfer teams. Ways to deal with this looking at their new teams form can be explored down the line.


Updates to TeamStats required:

Works fine if all 20 teams play in a gw, however if less play then it just ranks those that do play. And if there are doubles, then it needs to take the most recent (i.e. later gw) match.  

In [3]:
ff_data = PreprocessData('../data/2020-21/teams.csv', 
                      '../data/2021-22/teams.csv', 
                      '../data/2022-23/teams.csv', 
                      '../data/2020-21/gws/merged_gw.csv', 
                      '../data/2021-22/gws/merged_gw.csv', 
                      '../data/2022-23/gws/merged_gw.csv')

team_form = 5

preprocessed_data = ff_data.get_preprocessed_data()
ps = PlayerStats(preprocessed_data)
players_df = ps.process_data(team_form)
team_stats = TeamStats(players_df)
team_df = team_stats.calculate_team_df(team_form)
combineteamandplayer = CombineTeamAndPlayers(players_df, team_df, team_form)
final_df = combineteamandplayer.combine()
played = final_df[final_df['minutes_player'] > 0]

## How do the number of bps for a player affect the number of bonus points awarded?

In [4]:
#plotly scatter graph comparing bonus_player on the y axis to bps_player on the x axis
final_df['bonus_player_noise'] = final_df['bonus_player'] + np.random.normal(0, 0.05, final_df.shape[0])
fig = px.scatter(final_df, x="bps_player", y="bonus_player_noise", trendline="ols", opacity=0.5)
fig.update_layout(title = 'Bonus Points vs Bonus Points System', xaxis_title = 'Bonus Points System', yaxis_title = 'Bonus Points', title_x=0.5)
fig.show()
final_df = final_df.drop(columns=['bonus_player_noise'])

In [ ]:
fig.update_layout(title = 'Bonus Points vs Bonus Points System',

In [ ]:
 xaxis_title = 'Bonus Points System', yaxis_title = 'Bonus Points', title_x=0.5)
fig.show()

In [ ]:
 xaxis_title = 'Bonus Points System', yaxis_title = 'Bonus Points', title_x=0.5)
fig.show()

In [1]:
played = final_df[final_df['minutes_player'] > 0]
played.columns

NameError: name 'final_df' is not defined

## Harry Kane

Can HK's points/goals/assists be forecast based on his current form, his teams form and the form/quality of the opponents.

In [118]:
df = played[played['name_player'] == 'Harry Kane']

columns_to_drop = ['name_player',
                   'position_player',
                   'team_player',
                   'clean_sheets_player',
                   'creativity_player',
                   'fixture_player',
                   'goals_conceded_player',
                   'ict_index_player',
                   'influence_player',
                   'kickoff_time',
                   'own_goals_player',
                   'saves_player',
                   'selected_player',
                   'threat_player',
                   'transfers_balance_player',
                   'transfers_in_player',
                   'transfers_out_player',
                   'value_player',
                   'opponent_team',
                   'team_season_goals_against',
                   'team_season_goals_scored',
                   'total_points_season_player_team',
                   'total_goals_season_player_team',
                   'total_goals_against_season_player_team',
                   'season_goal_difference_player_team',
                   'total_points_season_opp_team',
                   'total_goals_season_opp_team',
                   'total_goals_against_season_opp_team',
                   'season_goal_difference_opp_team',
                   'penalties_missed_player',
                   'penalties_saved_player'
                   ]

model_data = df.drop(columns=columns_to_drop,axis=1)
model_data = model_data[model_data['season_matches_played_player_team']>0]
model_data = pd.get_dummies(model_data, columns=['season'], drop_first=True, prefix='season')
model_data = model_data.drop(columns=['season_matches_played_player_team',
       'season_matches_played_opp_team','last_5_team_match_points','last_5_games_points_player','season_goal_difference_per_match_player_team',
       'season_goal_difference_per_match_opp_team'],axis=1)

y = model_data['total_points_player']
X = model_data.drop(columns = ['total_points_player','assists_player', 'bonus_player', 'bps_player', 'goals_scored_player',
       'minutes_player','red_cards_player', 'was_home_player', 'yellow_cards_player','season_2021-22','season_2022-23'],axis=1)

# Define the pipeline
pipeline = Pipeline([
    ('scaler', StandardScaler()),
    ('regressor', RandomForestRegressor())
])

rmse_scorer = make_scorer(mean_squared_error, squared=False)


# Define the parameter grid for GridSearchCV
param_grid = {
    'regressor__n_estimators': [5,10, 50, 100],
    'regressor__max_depth': [None, 5, 10,15],
}

# Create the GridSearchCV object
grid_search = GridSearchCV(pipeline, param_grid, cv=5,scoring=rmse_scorer)

# Fit the model using GridSearchCV
grid_search.fit(X, y)

# Print the best parameters and score
print("Best parameters: ", grid_search.best_params_)
print("Best score: ", grid_search.best_score_)
print("Best estimator: ", grid_search.best_estimator_)

X.columns

Best parameters:  {'regressor__max_depth': 10, 'regressor__n_estimators': 5}
Best score:  5.381640418630588
Best estimator:  Pipeline(steps=[('scaler', StandardScaler()),
                ('regressor',
                 RandomForestRegressor(max_depth=10, n_estimators=5))])


Index(['last_5_team_goals', 'last_5_player_goals', 'last_5_team_against',
       'last_5_ind_goals_ratio_player', 'last_5_ind_assists_ratio_player',
       'season_goals_per_match_player_team',
       'season_goals_against_per_match_player_team',
       'season_points_per_match_player_team',
       'last_5_team_match_points_opp_team', 'last_5_team_goals_opp_team',
       'last_5_team_against_opp_team', 'season_goals_per_match_opp_team',
       'season_goals_against_per_match_opp_team',
       'season_points_per_match_opp_team'],
      dtype='object')

...

Columns:
- name_player: Name of player
- position_player: Player's position
- Team_player: Team player plays for
- xP_player: DROP
- assists_player: Players match assists
- bonus_player: 3/2/1 bonus points awarded for player
- bps_player: Total bps for player for that match
- clean_sheets_player: Clean sheet or not awarded to that player for the part they played (only relevant to GK, DEF and MID)
- creativity_player: Player's creativity score for that match
- element_player: DROP
- fixture_player: ID for that particular match
- goals_conceeded_player: Goals conceeded by the team in that match while player on pitch (only relevant to GK and DEF)
- goals_scored_player: Goals scored by individual player in that match
- ict_index_player: Player's ict index for that match
- influence_player: Player's influence score for that match
- kickoff_time_player: Match kickoff time (RENAME)
- minutes_player: Minutes played by that individual player in that match
- opponent_team_id_player: DROP
- own_goals_player: Own goals scored by player in that match
- penalties_missed_player: Penalties missed by player in that match
- penalties_saved_player: Penalties saved by player (only relevant to GK's)
- red_cards_player: Red cards for that player in the match
- round_player: DROP
- saves_player: Saves made by player (only relevant to GK's)
- selected_player: Number of fpl players who selected this player
- team_a_score_player: DROP
- team_h_score_player: DROP
- threat_player: Player's threat score for that match
- total_points_player: Player fpl points for match
- transfers_balance_player: Net of transfers in/out before that GW
- transfers_in_player: Transfers in before that GW
- transfers_out_player: Transfers out before that GW
- value_player: Cost to buy player at time of match kickoff
- was_home_player: Was the player's team home or away
- yellow_cards_player: Yellow cards for that player in the match
- season_player: Season of the match (RENAME)
- opponent_team_player: Name of opponent team (RENAME)
- team_points_player: Points scored for league for players team (RENAME)
- team_goals_player: Goals scored by player's team (RENAME)
- team_goals_against_player: Goals scored against player's team (RENAME)
- order_player: DROP
- last_{num_matches}_team_match_points_player: Total match points scored for player's team over last {num_matches} matches (RENAME)
- last_{num_matches}_team_goals_player: Total goals scored by player's team over last {num_matches} matches (RENAME)
- last_{num_matches}_games_goals_player: Total goals scored by player over last {num_matches} matches (RENAME)
- last_{num_matches}_team_against_player: Total goals scored against player's team over last {num_matches} matches (RENAME)
- last_{num_matches}_ind_goals_ratio_player: Percentage of team goals scored by player over last {num_matches} matches
- last_{num_matches}_ind_assists_ratio_player: Percentage of team's assists scored by player over last {num_matches} matches
- order_player_team: DROP
- total_points_season_player_team: Total points scored before this match by the player's team this season 
- total_goals_season_player_team: Total goals scores before this match by the player's team this season
- total_goals_against_season_player_team: Total goals against player's team before this match
- goal_difference_player_team: Goal difference of players team before this match
- season_matches_played_player_team: Matches played so far in season before this match by player's team
- last_{num_matches}_team_match_points_player_team: DROP
- last_{num_matches}_team_goals_player_team: DROP
- last_{num_matches}_team_against_player_team: DROP
- was_home_opp_team: DROP
- team_points_opp_team: DROP
- order_opp_team: DROP
- total_goals_season_opp_team: Total points scored before this match by opponents
- total_goals_season_opp_team: Total goals score before this match by opponents
- total_goals_against_season_opp_team: Total goals conceeded before this match by opponents
- goal_difference_opp_team: Goal difference of opponents before this match
- season_matches_played_opp_team: Matches played by opponents this season so far before this match
- last_{num_matches}_team_match_points_opp_team: Points won by opponents in last {num_matches} games
- last_{num_matches}_team_goals_opp_team: Goals scored by opponents in last {num_matches} games
- last_{num_matches}_team_against_opp_team: Goals conceeded by opponents in last {num_matches} games

Need to go through the below and ensure columns are appropriately titled and not duplicated.

## Other Exploration

- Distribution of goals score by player
- Distribution of assists by player
- Distribution of assists by player depending on teammates
- Distribution of goals scored by team as a whole
- Distribution of goals/assists as a percentage of teams forecasted goals
- Distribution of BPS
- Expected bonus points
- Expected bonus points to get 1/2/3 points
- Expected minutes played

#### Multivariate Approach

How all the above are affected by:
- Opponent
- GW/time of season
- Recent form
- Essentially all other columns in preprocessed df 
- Multivariate approach to BPS

#### Advanced

- Other games in same game week, i.e. champions league


# Data Vis


In [8]:
def player_prepro(player, df):
    df = df[df['name'] == player]
    df.drop(columns=['GW', 'name', 'position','xP','element', 'transfers_in', 'transfers_out','ict_index','own_goals','round'], inplace=True)
    df['kickoff_time'] = pd.to_datetime(df['kickoff_time'])
    df['match_number'] = df['kickoff_time'].rank(method='dense')
    df['match_number'] = df['match_number'].astype(int)
    df = df.sort_values(by='match_number', ascending=True)
    return df

In [16]:
t = player_prepro('Ivan Toney', preprocessed_data)
univar = t[['match_number','total_points']]

# Split the dataset into training and testing sets
train_size = len(univar) - 3
train_df = univar[:train_size]
test_df = univar[train_size:]

# Train a linear regression model on the training set
model = LinearRegression()
model.fit(train_df[['match_number']], train_df['total_points'])

# Use the model to forecast the next 3 points
future_df = pd.DataFrame({'match_number': range(len(univar)+1, len(univar)+4)})
future_df['total_points_forecast'] = model.predict(future_df[['match_number']])

fig = px.scatter(t, x='kickoff_time', y='total_points', color='season', size='minutes', hover_data=['opponent_team'])
fig.show()

In [27]:
def player_points_dist(df, player1, player2):
    fig = px.histogram(df[df['name'] == player1], x="total_points", nbins=20, opacity=0.5, color_discrete_sequence=['blue'])
    fig.add_histogram(x=df[df['name'] == player2]['total_points'], nbins=20, opacity=0.5, marker_color='red')
    fig.show()


In [28]:
def points_dist_by_pos(df):
    fig = px.histogram(df, x='total_points', color='position', marginal='box', nbins=25,
                        opacity=0.7, # Set opacity of histogram boxes
                        labels={'total_points': 'Total Points', 'position': 'Position'}, # Change axis labels
                        title='Distribution of Points Scored by Position') # Change plot title
    fig.update_layout(
        font=dict(size=16), # Increase font size of all text
        legend=dict(title='Position', font=dict(size=14)), # Increase font size of legend title and labels
        xaxis=dict(title_font=dict(size=16)), # Increase font size of x-axis label
        yaxis=dict(title_font=dict(size=16)), # Increase font size of y-axis label
    )
    fig.show()

#points distribution by team the player plays for
def points_dist_by_team(df):
    fig = px.histogram(df, x='total_points', color='team', marginal='box', nbins=5)
    fig.update_layout(title='Distribution of points scored by team')
    fig.show()

In [29]:
player_points_dist(gws2223_played, 'Erling Haaland', 'Harry Kane')

ValueError: Invalid property specified for object of type plotly.graph_objs.Histogram: 'nbins'

Did you mean "nbinsx"?

    Valid properties:
        alignmentgroup
            Set several traces linked to the same position axis or
            matching axes to the same alignmentgroup. This controls
            whether bars compute their positional range dependently
            or independently.
        autobinx
            Obsolete: since v1.42 each bin attribute is auto-
            determined separately and `autobinx` is not needed.
            However, we accept `autobinx: true` or `false` and will
            update `xbins` accordingly before deleting `autobinx`
            from the trace.
        autobiny
            Obsolete: since v1.42 each bin attribute is auto-
            determined separately and `autobiny` is not needed.
            However, we accept `autobiny: true` or `false` and will
            update `ybins` accordingly before deleting `autobiny`
            from the

In [16]:
haaland = gws2223_played[gws2223_played['name'] == 'Erling Haaland']

In [73]:
teams2122 = teams2122.rename(columns= {'Team': 'team', 'Player': 'name'})


In [72]:
data2223 = preprocess_data(players2223,teams2223)


In [38]:
data2122 = preprocess_data(players2122,teams2122)

In [71]:
data2122['team'] = data2122.index


In [40]:
players2122['full_name'] = players2122[['first_name','second_name']].apply(lambda x: x.str.cat(sep=' '), axis=1)

In [68]:
#fig = px.scatter(data2223, x='now_cost', y='total_points',color='element_type' ,hover_data='full_name')
#fig.show()

In [69]:
#fig = px.scatter_3d(data2223, x='now_cost', y='points_to_price_ratio', z='total_points',color='element_type', hover_data='full_name')
#fig.show()

In [70]:
#best_team_2122 = optimise_team(data2122)

In [48]:
# create scatter plot for data2122 with blue points
fig = px.scatter(data2122, x='now_cost', y='total_points', hover_data='full_name', color_discrete_sequence=['blue'], labels={'total_points': 'Total Points (2021/22)'})

# add scatter plot for data2223 with red points
fig.add_trace(px.scatter(data2223, x='now_cost', y='total_points', hover_data='full_name', color_discrete_sequence=['red'], labels={'total_points': 'Total Points (2022/23)'}).data[0])

# update marker settings
fig.update_traces(marker_opacity=0.5, marker_size=8, selector=dict(type='scatter'), showlegend = True)

# add legend
fig.update_layout(
    legend=dict(title='', orientation='h', yanchor='bottom', y=1.02, xanchor='right', x=1),
    xaxis=dict(range=[35, max(data2122['now_cost'].max(), data2223['now_cost'].max())]),
    yaxis=dict(range=[-10, max(data2122['total_points'].max(), data2223['total_points'].max())])
)

# show plot
fig.show()


In [63]:
class TeamStats_draft_all_teams:
    def __init__(self, match_df):
        self.match_df = match_df
        self.team_df = None
    
    def calculate_team_df(self, num_matches):
        team_df_copy = self.match_df.copy()

        team_df_copy = team_df_copy.groupby(['season', 'GW', 'fixture', 'team']).agg({
            'team_goals': 'first',
            'team_goals_against': 'first',
            'was_home': 'first',
            'opponent_team': 'first',
            'team_points': 'first',
            'order': 'first'
        }).reset_index()

        # Create a DataFrame with all unique teams and game weeks
        unique_teams = team_df_copy['team'].unique()
        unique_game_weeks = team_df_copy['GW'].unique()
        unique_seasons = team_df_copy['season'].unique()
        all_team_gw = pd.MultiIndex.from_product([unique_seasons, unique_game_weeks, unique_teams], names=['season', 'GW', 'team']).to_frame(index=False)

        # Merge the all_team_gw DataFrame with the existing team_df_copy
        team_df_copy = pd.merge(all_team_gw, team_df_copy, on=['season', 'GW', 'team'], how='left')

        team_df_copy['team_points'] = team_df_copy['team_points'].fillna(0)
        team_df_copy['team_goals'] = team_df_copy['team_goals'].fillna(0)
        team_df_copy['team_goals_against'] = team_df_copy['team_goals_against'].fillna(0)

        team_df_copy['total_points_season'] = team_df_copy.groupby(['season', 'team'])['team_points'].cumsum() - team_df_copy['team_points']

        team_df_copy['total_goals_season'] = team_df_copy.groupby(['season', 'team'])['team_goals'].cumsum() - team_df_copy['team_goals']

        team_df_copy['total_goals_against_season'] = team_df_copy.groupby(['season', 'team'])['team_goals_against'].cumsum() - team_df_copy['team_goals_against']

        team_df_copy['goal_difference'] = team_df_copy['total_goals_season'] - team_df_copy['total_goals_against_season']

        # Calculate league position by game week
        team_df_copy['league_position'] = team_df_copy.groupby(['season', 'GW'])['total_points_season'].rank(ascending=False, method='min')

        team_df_copy['season_matches_played'] = team_df_copy.groupby(['season', 'team'])['fixture'].cumcount()

        team_df_copy = team_df_copy.groupby(['team'], group_keys=False).apply(self._rolling_position_form, num_matches).reset_index(drop=True)

        self.team_df = team_df_copy

        return team_df_copy


    def _rolling_position_form(self, group, num_matches):
        df = group.sort_values(by='order', ascending=True)
        rolling_sum = df['league_position'].rolling(window=num_matches, min_periods=1).sum().shift(1)
        rolling_count = df['league_position'].rolling(window=num_matches, min_periods=1).count().shift(1)
        df[f'last_{num_matches}_games_league_position'] = ((rolling_sum / rolling_count)).fillna(0)
        return df